# Contour Monte Carlo: Growth factor model
This Julia notebook demonstrates how to perform Contour Monte Carlo to estimate cell population heterogeneity for the growth factor model in Lambert et al., 2019. Note that the code uses the `RCall` Julia package to call R, in order to use the vine copula kernel density estimation available in the R package `kdevine`.

Functions needed for CMC.

In [1]:
using RCall, Compat, Random, Distributions, Plots, DifferentialEquations, LinearAlgebra, Plots, DelimitedFiles

R"library(kdevine)"
    
function f_solve(f_deriv, initial, tspan, parameters)
    prob = ODEProblem(f_deriv, initial, tspan, parameters)
    sol = solve(prob)
    return sol
end

function f_sample_solve_uniform(num_samples, population_sample, times_solve, tspan, f_solve, f_deriv, bounds, initial)
    n_params = size(bounds)[1]
    samples = zeros((num_samples, n_params))
    for i = 1:n_params
        samples[:, i] = rand(Uniform(bounds[i, 1], bounds[i, 2]), num_samples)
    end
    mOutputs = zeros((num_samples, length(population_sample)))
    for i in 1:num_samples
        sol = f_solve(f_deriv, initial, tspan, samples[i, :]);
        for j = 1:length(population_sample)
           mOutputs[i, j] = sol(times_solve[j], idxs=population_sample[j])
        end
    end
    return mOutputs
end

function f_sample_solve_uniform_uncertain_inits(num_samples, population_sample, times_solve,
        tspan, f_solve, f_deriv, bounds, nparams, ninits)
    n_params = size(bounds)[1]
    samples = zeros((num_samples, n_params))
    for i = 1:n_params
        samples[:, i] = rand(Uniform(bounds[i, 1], bounds[i, 2]), num_samples)
    end
    mOutputs = zeros((num_samples, length(population_sample)))
    for i in 1:num_samples
        sol = f_solve(f_deriv, samples[i, (nparams + 1):(nparams + ninits)], tspan, samples[i, 1:nparams]);
        for j = 1:length(population_sample)
           mOutputs[i, j] = sol(times_solve[j], idxs=population_sample[j])
        end
    end
    return mOutputs
end

function f_estimate_kdevine(mOutputs)
    @rput mOutputs
    R"fit <- kdevine(mOutputs)"
    R"saveRDS(fit, '../data/vine_fit.RDS')"
end

function dkdevine(params)
    @rput params
    R"z <- dkdevine(params, fit)"
    @rget z
    return z
end

function load_dkdevine_fit()
    R"z <- readRDS('../data/vine_fit.RDS')"
    @rget z
    return z
end

function f_step_bounds(vCurrent, bounds, sigma)
    vProposed = zeros(size(bounds)[1])
    for i = 1:length(vProposed)
        temp = (rand(Normal(vCurrent[i] - bounds[i, 1], sigma[i]), 1)[1] % (bounds[i, 2] - bounds[i, 1]))
        if temp < 0
            temp += bounds[i, 2]
        else
            temp += bounds[i, 1]
        end
        vProposed[i] = temp
    end
    return vProposed
end

function f_step_bounds_simple(vCurrent, bounds, sigma)
    vProposed = zeros(size(bounds)[1])
    for i = 1:length(vProposed)
        temp = rand(Normal(vCurrent[i], sigma[i]), 1)[1]
        vProposed[i] = temp
    end
    return vProposed
end

function f_mcmc_uniform_uncertain_ints(num_samples, target_fn, f_dkdevine, sigma,
        population_sample, times_solve, tspan, f_solve, f_deriv, bounds, initial_inputs, nparams, ninits)
    mInputs = zeros((num_samples, size(bounds)[1]))
    mOutputs = zeros((num_samples, length(population_sample)))
    vOutputs_temp = zeros(length(population_sample))
    vLogPDF = zeros(num_samples)
    vContour = zeros(num_samples)
    # initial points
    mInputs[1, :] = initial_inputs
    for j = 1:length(population_sample)
        sol = f_solve(f_deriv, mInputs[1, (nparams + 1):(nparams + ninits)], tspan, mInputs[1, 1:nparams]);
        mOutputs[1, j] = sol(times_solve[j], idxs=population_sample[j])
    end
    log_pdf_current = target_fn(mOutputs[1, :])
    log_contour_current = log(f_dkdevine(mOutputs[1, :]))
    # MCMC
    log_a = 0.0
    sigma = Matrix(Diagonal(sigma.^2))
    mu = initial_inputs
    for i = 2:num_samples
        if i <= (100 * (nparams + ninits))
            vProposed = rand(MvNormal(mInputs[i - 1, :], sigma), 1)
            if (sum(vProposed .< bounds[:, 1]) > 0) || (sum(vProposed .> bounds[:, 2]) > 0)
                mInputs[i, :] = mInputs[i - 1, :]
                mOutputs[i, :] = mOutputs[i - 1, :]
                accepted = 0.0
            else
                sol = f_solve(f_deriv, vProposed[(nparams + 1):(nparams + ninits)], tspan, vProposed[1:nparams]);
                for j = 1:length(population_sample)
                    vOutputs_temp[j] = sol(times_solve[j], idxs=population_sample[j]);
                end
                log_pdf_proposed = target_fn(vOutputs_temp)
                log_contour_proposed = log(f_dkdevine(vOutputs_temp))
                log_r = ((log_pdf_proposed + log_contour_current) -
                         (log_pdf_current + log_contour_proposed))
                if (log_r > log(rand(Uniform(), 1)[1])) && (log_contour_proposed > -4)
                    mInputs[i, :] = vProposed
                    mOutputs[i, :] = vOutputs_temp
                    log_pdf_current = log_pdf_proposed
                    log_contour_current = log_contour_proposed
                    accepted = 1.0
                else
                    mInputs[i, :] = mInputs[i - 1, :]
                    mOutputs[i, :] = mOutputs[i - 1, :]
                    accepted = 0.0
                end
            end
            vLogPDF[i] = log_pdf_current
            vContour[i] = log_contour_current
        else
            s = i - (100 * (nparams + ninits))
            gamma = (s + 1)^(-0.6)
            vProposed = rand(MvNormal(mInputs[i - 1, :], Matrix(Hermitian(sigma)) * exp(log_a)), 1)
            if (sum(vProposed .< bounds[:, 1]) > 0) || (sum(vProposed .> bounds[:, 2]) > 0)
                mInputs[i, :] = mInputs[i - 1, :]
                mOutputs[i, :] = mOutputs[i - 1, :]
                accepted = 0.0
            else
                sol = f_solve(f_deriv, vProposed[(nparams + 1):(nparams + ninits)], tspan, vProposed[1:nparams]);
                for j = 1:length(population_sample)
                    vOutputs_temp[j] = sol(times_solve[j], idxs=population_sample[j]);
                end
                log_pdf_proposed = target_fn(vOutputs_temp)
                log_contour_proposed = log(f_dkdevine(vOutputs_temp))
                log_r = ((log_pdf_proposed + log_contour_current) -
                         (log_pdf_current + log_contour_proposed))
                if (log_r > log(rand(Uniform(), 1)[1])) && (log_contour_proposed > -4)
                    mInputs[i, :] = vProposed
                    mOutputs[i, :] = vOutputs_temp
                    log_pdf_current = log_pdf_proposed
                    log_contour_current = log_contour_proposed
                    accepted = 1.0
                else
                    mInputs[i, :] = mInputs[i - 1, :]
                    mOutputs[i, :] = mOutputs[i - 1, :]
                    accepted = 0.0
                end
            end
            vLogPDF[i] = log_pdf_current
            vContour[i] = log_contour_current
            sigma = (1 - gamma) * sigma + gamma * (mInputs[i, :] - mu) * (mInputs[i, :] - mu)'
            mu = (1 - gamma) * mu + gamma * mInputs[i, :]
            log_a += gamma * (accepted - 0.25)
        end
    end
    return Dict("inputs" => mInputs, "outputs" => mOutputs, "log_pdf" => vLogPDF, "contour_volume" => vContour)
end

function f_mcmc_uniform(num_samples, target_fn, f_dkdevine, sigma,
        population_sample, times_solve, tspan, f_solve, f_deriv, bounds, initial_inputs, initial)
    mInputs = zeros((num_samples, size(bounds)[1]))
    mOutputs = zeros((num_samples, length(population_sample)))
    vOutputs_temp = zeros(length(population_sample))
    vLogPDF = zeros(num_samples)
    vContour = zeros(num_samples)
    # initial points
    mInputs[1, :] = initial_inputs
    for j = 1:length(population_sample)
        sol = f_solve(f_deriv, initial, tspan, mInputs[1, :]);
        mOutputs[1, j] = sol(times_solve[j], idxs=population_sample[j])
    end
    log_pdf_current = target_fn(mOutputs[1, :])
    log_contour_current = log(f_dkdevine(mOutputs[1, :]))
    # MCMC
    log_a = 0.0
    sigma = Matrix(Diagonal(sigma.^2))
    mu = initial_inputs
    for i = 2:num_samples
        if i <= (100 * length(initial_inputs))
            vProposed = rand(MvNormal(mInputs[i - 1, :], sigma), 1)
            if (sum(vProposed .< bounds[:, 1]) > 0) || (sum(vProposed .> bounds[:, 2]) > 0)
                mInputs[i, :] = mInputs[i - 1, :]
                mOutputs[i, :] = mOutputs[i - 1, :]
                accepted = 0.0
            else
                sol = f_solve(f_deriv, initial, tspan, vProposed);
                for j = 1:length(population_sample)
                    vOutputs_temp[j] = sol(times_solve[j], idxs=population_sample[j]);
                end
                log_pdf_proposed = target_fn(vOutputs_temp)
                log_contour_proposed = log(f_dkdevine(vOutputs_temp))
                log_r = ((log_pdf_proposed + log_contour_current) -
                         (log_pdf_current + log_contour_proposed))
                if (log_r > log(rand(Uniform(), 1)[1])) && (log_contour_proposed > -4)
                    mInputs[i, :] = vProposed
                    mOutputs[i, :] = vOutputs_temp
                    log_pdf_current = log_pdf_proposed
                    log_contour_current = log_contour_proposed
                    accepted = 1.0
                else
                    mInputs[i, :] = mInputs[i - 1, :]
                    mOutputs[i, :] = mOutputs[i - 1, :]
                    accepted = 0.0
                end
            end
            vLogPDF[i] = log_pdf_current
            vContour[i] = log_contour_current
        else
            s = i - (100 * length(initial_inputs))
            gamma = (s + 1)^(-0.6)
            vProposed = rand(MvNormal(mInputs[i - 1, :], Matrix(Hermitian(sigma)) * exp(log_a)), 1)
            if (sum(vProposed .< bounds[:, 1]) > 0) || (sum(vProposed .> bounds[:, 2]) > 0)
                mInputs[i, :] = mInputs[i - 1, :]
                mOutputs[i, :] = mOutputs[i - 1, :]
                accepted = 0.0
            else
                sol = f_solve(f_deriv, initial, tspan, vProposed);
                for j = 1:length(population_sample)
                    vOutputs_temp[j] = sol(times_solve[j], idxs=population_sample[j]);
                end
                log_pdf_proposed = target_fn(vOutputs_temp)
                log_contour_proposed = log(f_dkdevine(vOutputs_temp))
                log_r = ((log_pdf_proposed + log_contour_current) -
                         (log_pdf_current + log_contour_proposed))
                if (log_r > log(rand(Uniform(), 1)[1])) && (log_contour_proposed > -4)
                    mInputs[i, :] = vProposed
                    mOutputs[i, :] = vOutputs_temp
                    log_pdf_current = log_pdf_proposed
                    log_contour_current = log_contour_proposed
                    accepted = 1.0
                else
                    mInputs[i, :] = mInputs[i - 1, :]
                    mOutputs[i, :] = mOutputs[i - 1, :]
                    accepted = 0.0
                end
            end
            vLogPDF[i] = log_pdf_current
            vContour[i] = log_contour_current
            sigma = (1 - gamma) * sigma + gamma * (mInputs[i, :] - mu) * (mInputs[i, :] - mu)'
            mu = (1 - gamma) * mu + gamma * mInputs[i, :]
            log_a += gamma * (accepted - 0.25)
        end
    end
    return Dict("inputs" => mInputs, "outputs" => mOutputs, "log_pdf" => vLogPDF, "contour_volume" => vContour)
end

function f_log_pdf(v_values, v_dist)
    log_pdf = 0.0
    k = 1
    for val in v_values
        log_pdf += logpdf(v_dist[k], val)
        k += 1
    end
    return log_pdf
    end

function f_mcmc_uniform_multiple(nchains, num_samples, target_fn, f_dkdevine, sigma,
        population_sample, times_solve, tspan, f_solve, f_deriv, bounds, initial_inputs, initial)
    vResults = []
    for i = 1:nchains
         push!(vResults, f_mcmc_uniform(num_samples, target_fn, f_dkdevine, sigma,
        population_sample, times_solve, tspan, f_solve, f_deriv, bounds, initial_inputs, initial))
    end
    return vResults
end

function f_mcmc_uniform_uncertain_ints_multiple(nchains, num_samples, target_fn, f_dkdevine, sigma,
        population_sample, times_solve, tspan, f_solve, f_deriv, bounds, initial_inputs, nparams, ninits)
    vResults = []
    for i = 1:nchains
         push!(vResults, f_mcmc_uniform_uncertain_ints(num_samples, target_fn, f_dkdevine, sigma,
        population_sample, times_solve, tspan, f_solve, f_deriv, bounds, initial_inputs, nparams, ninits))
    end
    return vResults
end

function f_between(vResults)
    nchains = length(vResults)
    inputs = vResults[1]["inputs"];
    nparams = size(inputs)[2];
    mMeans = zeros((nchains, nparams));
    for i = 1:nchains
        inputs = vResults[i]["inputs"];
        for j = 1:nparams
            mMeans[i, j] = mean(inputs[:, j]);
        end
    end
    t = size(inputs)[1];
    vOverallMean = mean(mMeans, dims=1);
    vVar = (t / (nchains - 1)) * sum((mMeans .- vOverallMean).^2, dims=1);
    return vVar
end

function f_within(vResults)
    nchains = length(vResults)
    inputs = vResults[1]["inputs"];
    nparams = size(inputs)[2];
    mVars = zeros((nchains, nparams));
    for i = 1:nchains
        inputs = vResults[i]["inputs"];
        for j = 1:nparams
            mVars[i, j] = var(inputs[:, j]);
        end
    end
    return mean(mVars, dims=1)
end

function f_rhat(vResults)
    nchains = length(vResults)
    inputs = vResults[1]["inputs"];
    nparams = size(inputs)[2];
    t = size(inputs)[1];
    vWithin = f_within(vResults);
    vBetween = f_between(vResults);
    return sqrt.((vBetween ./ t + vWithin) ./ vWithin)
end


R version 3.4.2 (2017-09-28) -- "Short Summer"
Copyright (C) 2017 The R Foundation for Statistical Computing
Platform: x86_64-w64-mingw32/x64 (64-bit)

R is free software and comes with ABSOLUTELY NO WARRANTY.
You are welcome to redistribute it under certain conditions.
Type 'license()' or 'licence()' for distribution details.

R is a collaborative project with many contributors.
Type 'contributors()' for more information and
'citation()' on how to cite R or R packages in publications.

Type 'demo()' for some demos, 'help()' for on-line help, or
'help.start()' for an HTML browser interface to help.
Type 'q()' to quit R.



┌ Warning: RCall.jl: Warning: package 'kdevine' was built under R version 3.4.4
│ The kdevine package is no longer actively developed. Consider using 
│    - the 'kde1d' package for marginal estimation, 
│    - the functions vine() and vinecop() from the 'rvinecopulib' 
│      package as replacements for kdevine() and kdevincop().
└ @ RCall C:\Users\bclamber\.julia\packages\RCall\ffM0W\src\io.jl:113


f_rhat (generic function with 1 method)

## Growth factor model
### Using uniform priors

Estimate contour volumes.

In [2]:
function deriv_growth_factor(dxdt, y, p, t)
    RT=p[1]; kdegstar=p[2]; k1=p[3];
    kminus1=p[4]; kdeg=p[5]; L=p[6]; 
    R=y[1]; P=y[2];
    kdel = RT * kdeg;
    dxdt[1] = kdel - k1 * L * R + kminus1 * P - kdeg * R;
    dxdt[2] = k1 * L * R - kminus1 * P - kdegstar * P
end

# number of independent samples to take from bounds (used more in paper)
ncontourvolsteps = 1000

# bounds of parameters (uniform prior within bounds assumed)
mBounds = [[2.5 * 10^5 8 * 10^5]; [0.1 0.5]; [0.25 3]; [2 20]; [0.005 0.03]];

tspan = (0.0, 20.0)
initial_states = [0.0; 0.0];
populations_observed = [2, 2]
times_observed = [10, 10]

function f_sample_solve_uniform_growth_factor(num_samples, population_sample, times_solve,
        tspan, f_solve, f_deriv, bounds, initial)
    n_params = size(bounds)[1]
    samples = zeros((num_samples, n_params))
    vL = [2, 10]
    for i = 1:n_params
        samples[:, i] = rand(Uniform(bounds[i, 1], bounds[i, 2]), num_samples)
    end
    mOutputs = zeros((num_samples, length(population_sample)))
    for i in 1:num_samples
        for j = 1:length(population_sample)
            sol = f_solve(f_deriv, initial, tspan, vcat(samples[i, :], [vL[j]]));
            mOutputs[i, j] = sol(times_solve[j], idxs=population_sample[j])
        end
    end
    return mOutputs
end

mOutputs = @time f_sample_solve_uniform_growth_factor(ncontourvolsteps, populations_observed, times_observed,
    tspan, f_solve, deriv_growth_factor, mBounds, initial_states);

@time f_estimate_kdevine(mOutputs);

 13.331536 seconds (35.00 M allocations: 1.783 GiB, 6.67% gc time)
  0.741438 seconds (222.17 k allocations: 11.293 MiB, 0.92% gc time)


Perform MCMC.

In [6]:
function f_mcmc_uniform_growth_factor(num_samples, target_fn, f_dkdevine, sigma,
        population_sample, times_solve, tspan, f_solve, f_deriv, bounds, initial_inputs, initial)
    mInputs = zeros((num_samples, size(bounds)[1]))
    mOutputs = zeros((num_samples, length(population_sample)))
    vOutputs_temp = zeros(length(population_sample))
    vLogPDF = zeros(num_samples)
    vContour = zeros(num_samples)
    vL = [2, 10]
    # initial points
    mInputs[1, :] = initial_inputs
    for j = 1:length(population_sample)
        sol = f_solve(f_deriv, initial, tspan, vcat(mInputs[1, :], [vL[j]]));
        mOutputs[1, j] = sol(times_solve[j], idxs=population_sample[j])
    end
    log_pdf_current = target_fn(mOutputs[1, :])
    log_contour_current = log(f_dkdevine(mOutputs[1, :]))
    # MCMC
    log_a = 0.0
    sigma = Matrix(Diagonal(sigma.^2))
    mu = initial_inputs
    for i = 2:num_samples
        if i <= (100 * length(initial_inputs))
            vProposed = rand(MvNormal(mInputs[i - 1, :], sigma), 1)
            if (sum(vProposed .< bounds[:, 1]) > 0) || (sum(vProposed .> bounds[:, 2]) > 0)
                mInputs[i, :] = mInputs[i - 1, :]
                mOutputs[i, :] = mOutputs[i - 1, :]
                accepted = 0.0
            else
                for j = 1:length(population_sample)
                    sol = f_solve(f_deriv, initial, tspan, vcat(vProposed, [vL[j]]));
                    vOutputs_temp[j] = sol(times_solve[j], idxs=population_sample[j]);
                end
                log_pdf_proposed = target_fn(vOutputs_temp)
                log_contour_proposed = log(f_dkdevine(vOutputs_temp))
                log_r = ((log_pdf_proposed + log_contour_current) -
                         (log_pdf_current + log_contour_proposed))
                if (log_r > log(rand(Uniform(), 1)[1])) && (log_contour_proposed > -30)
                    mInputs[i, :] = vProposed
                    mOutputs[i, :] = vOutputs_temp
                    log_pdf_current = log_pdf_proposed
                    log_contour_current = log_contour_proposed
                    accepted = 1.0
                else
                    mInputs[i, :] = mInputs[i - 1, :]
                    mOutputs[i, :] = mOutputs[i - 1, :]
                    accepted = 0.0
                end
            end
            vLogPDF[i] = log_pdf_current
            vContour[i] = log_contour_current
        else
            s = i - (100 * length(initial_inputs))
            gamma = (s + 1)^(-0.6)
            vProposed = rand(MvNormal(mInputs[i - 1, :], Matrix(Hermitian(sigma)) * exp(log_a)), 1)
            if (sum(vProposed .< bounds[:, 1]) > 0) || (sum(vProposed .> bounds[:, 2]) > 0)
                mInputs[i, :] = mInputs[i - 1, :]
                mOutputs[i, :] = mOutputs[i - 1, :]
                accepted = 0.0
            else
                for j = 1:length(population_sample)
                    sol = f_solve(f_deriv, initial, tspan, vcat(vProposed, [vL[j]]));
                    vOutputs_temp[j] = sol(times_solve[j], idxs=population_sample[j]);
                end
                log_pdf_proposed = target_fn(vOutputs_temp)
                log_contour_proposed = log(f_dkdevine(vOutputs_temp))
                log_r = ((log_pdf_proposed + log_contour_current) -
                         (log_pdf_current + log_contour_proposed))
                if (log_r > log(rand(Uniform(), 1)[1])) && (log_contour_proposed > -30)
                    mInputs[i, :] = vProposed
                    mOutputs[i, :] = vOutputs_temp
                    log_pdf_current = log_pdf_proposed
                    log_contour_current = log_contour_proposed
                    accepted = 1.0
                else
                    mInputs[i, :] = mInputs[i - 1, :]
                    mOutputs[i, :] = mOutputs[i - 1, :]
                    accepted = 0.0
                end
            end
            vLogPDF[i] = log_pdf_current
            vContour[i] = log_contour_current
            sigma = (1 - gamma) * sigma + gamma * (mInputs[i, :] - mu) * (mInputs[i, :] - mu)'
            mu = (1 - gamma) * mu + gamma * mInputs[i, :]
            log_a += gamma * (accepted - 0.25)
        end
    end
    return Dict("inputs" => mInputs, "outputs" => mOutputs, "log_pdf" => vLogPDF, "contour_volume" => vContour)
end

function f_mcmc_uniform_growth_factor_multiple(nchains, num_samples, target_fn, f_dkdevine, sigma,
        population_sample, times_solve, tspan, f_solve, f_deriv, bounds, initial_inputs, initial)
    vResults = []
    for i = 1:nchains
         push!(vResults, f_mcmc_uniform_growth_factor(num_samples, target_fn, f_dkdevine, sigma,
        population_sample, times_solve, tspan, f_solve, f_deriv, bounds, initial_inputs, initial))
    end
    return vResults
end

# number of chains (not run in parallel due to RCall)
nchains = 4
# number of MCMC steps (adapting after 100 * length(initial_parametesr))
nsamples = 10000
# MCMC initial (before adaptation) step sizes
sigma = [1.0 * 10^5, 0.05, 0.025, 0.5, 0.0005];
# initial parameters
initial_parameters = [4.0 * 10^5; 0.25; 1.0; 10; 0.01]
dist = MvNormal([2.0 * 10^4, 3.0 * 10^4], [[100000.0 0.0]; [0.0 100000.0]])
vResults = @time f_mcmc_uniform_growth_factor_multiple(nchains, nsamples, x -> logpdf(dist, x), dkdevine,
                    sigma, populations_observed, times_observed, tspan,
                    f_solve, deriv_growth_factor,
                    mBounds, initial_parameters, initial_states);

131.450731 seconds (61.29 M allocations: 4.728 GiB, 1.10% gc time)


Check for convergence of Markov chains.

In [7]:
f_rhat(vResults)

1×5 Array{Float64,2}:
 1.007  1.01485  1.02661  1.01276  1.02895

Plot output samples from posterior distribution.

In [8]:
scatter(vResults[1]["outputs"][1000:end, 1], vResults[1]["outputs"][1000:end, 2])

### Gaussian priors

Contour volume estimation.

In [10]:
function f_sample_solve_nonuniform_growth_factor(num_samples, population_sample, times_solve,
        tspan, f_solve, f_deriv, prior_params, initial)
    n_params = size(prior_params)[1]
    samples = zeros((num_samples, n_params))
    vL = [2, 10]
    for i = 1:n_params
        samples[:, i] = rand(Normal(prior_params[i, 1], prior_params[i, 2]), num_samples)
    end
    mOutputs = zeros((num_samples, length(population_sample)))
    for i in 1:num_samples
        for j = 1:length(population_sample)
            sol = f_solve(f_deriv, initial, tspan, vcat(samples[i, :], [vL[j]]));
            mOutputs[i, j] = sol(times_solve[j], idxs=population_sample[j])
        end
    end
    return mOutputs
end

# number of independent samples to take from bounds
ncontourvolsteps = 100000

# bounds of parameters (Gaussian prior within [mean, sd])
prior_params = [[5 * 10^5 10^5]; [0.3 0.1]; [0.5 0.1]; [3 1]; [0.02 0.005]];

tspan = (0.0, 20.0)
initial_states = [0.0; 0.0];
populations_observed = [2, 2]
times_observed = [10, 10]


mOutputs = @time f_sample_solve_nonuniform_growth_factor(ncontourvolsteps, populations_observed, times_observed,
    tspan, f_solve, deriv_growth_factor, prior_params, initial_states);

@time f_estimate_kdevine(mOutputs);

 48.848221 seconds (177.17 M allocations: 13.224 GiB, 8.34% gc time)
1328.331668 seconds (112 allocations: 3.453 KiB)


Perform MCMC.

In [11]:
function log_prior(prior_params, vX)
    log_prior1 = 0.0
    for j = 1:length(vX)
        log_prior1 += logpdf(Normal(prior_params[j, 1], prior_params[j, 2]), vX[j])
    end
    return log_prior1
end
function f_mcmc_nonuniform_growth_factor(num_samples, target_fn, f_dkdevine, sigma,
        population_sample, times_solve, tspan, f_solve, f_deriv, prior_params, initial_inputs, initial)
    mInputs = zeros((num_samples, size(prior_params)[1]))
    mOutputs = zeros((num_samples, length(population_sample)))
    vOutputs_temp = zeros(length(population_sample))
    vLogPDF = zeros(num_samples)
    vContour = zeros(num_samples)
    vL = [2, 10]
    # initial points
    mInputs[1, :] = initial_inputs
    for j = 1:length(population_sample)
        sol = f_solve(f_deriv, initial, tspan, vcat(mInputs[1, :], [vL[j]]));
        mOutputs[1, j] = sol(times_solve[j], idxs=population_sample[j])
    end
    log_pdf_current = target_fn(mOutputs[1, :])
    log_contour_current = log(f_dkdevine(mOutputs[1, :]))
    # MCMC
    log_a = 0.0
    sigma = Matrix(Diagonal(sigma.^2))
    mu = initial_inputs
    for i = 2:num_samples
        if i <= (100 * length(initial_inputs))
            vProposed = rand(MvNormal(mInputs[i - 1, :], sigma), 1)
            for j = 1:length(population_sample)
                sol = f_solve(f_deriv, initial, tspan, vcat(vProposed, [vL[j]]));
                vOutputs_temp[j] = sol(times_solve[j], idxs=population_sample[j]);
            end
            log_prior_proposed = log_prior(prior_params, vProposed)
            log_prior_current = log_prior(prior_params, mInputs[i - 1, :])
            log_pdf_proposed = target_fn(vOutputs_temp)
            log_contour_proposed = log(f_dkdevine(vOutputs_temp))
            log_r = ((log_pdf_proposed + log_contour_current + log_prior_proposed) -
                     (log_pdf_current + log_contour_proposed + log_prior_current))
            if (log_r > log(rand(Uniform(), 1)[1])) && (log_contour_proposed > -30)
                mInputs[i, :] = vProposed
                mOutputs[i, :] = vOutputs_temp
                log_pdf_current = log_pdf_proposed
                log_contour_current = log_contour_proposed
                accepted = 1.0
            else
                mInputs[i, :] = mInputs[i - 1, :]
                mOutputs[i, :] = mOutputs[i - 1, :]
                accepted = 0.0
            end
            vLogPDF[i] = log_pdf_current
            vContour[i] = log_contour_current
        else
            s = i - (100 * length(initial_inputs))
            gamma = (s + 1)^(-0.6)
            vProposed = rand(MvNormal(mInputs[i - 1, :], Matrix(Hermitian(sigma)) * exp(log_a)), 1)
            for j = 1:length(population_sample)
                sol = f_solve(f_deriv, initial, tspan, vcat(vProposed, [vL[j]]));
                vOutputs_temp[j] = sol(times_solve[j], idxs=population_sample[j]);
            end
            log_prior_proposed = log_prior(prior_params, vProposed)
            log_prior_current = log_prior(prior_params, mInputs[i - 1, :])
            log_pdf_proposed = target_fn(vOutputs_temp)
            log_contour_proposed = log(f_dkdevine(vOutputs_temp))
            log_r = ((log_pdf_proposed + log_contour_current + log_prior_proposed) -
                     (log_pdf_current + log_contour_proposed + log_prior_current))
            if (log_r > log(rand(Uniform(), 1)[1])) && (log_contour_proposed > -30)
                mInputs[i, :] = vProposed
                mOutputs[i, :] = vOutputs_temp
                log_pdf_current = log_pdf_proposed
                log_contour_current = log_contour_proposed
                accepted = 1.0
            else
                mInputs[i, :] = mInputs[i - 1, :]
                mOutputs[i, :] = mOutputs[i - 1, :]
                accepted = 0.0
            end
            vLogPDF[i] = log_pdf_current
            vContour[i] = log_contour_current
            sigma = (1 - gamma) * sigma + gamma * (mInputs[i, :] - mu) * (mInputs[i, :] - mu)'
            mu = (1 - gamma) * mu + gamma * mInputs[i, :]
            log_a += gamma * (accepted - 0.25)
        end
    end
    return Dict("inputs" => mInputs, "outputs" => mOutputs, "log_pdf" => vLogPDF, "contour_volume" => vContour)
end

function f_mcmc_nonuniform_growth_factor_multiple(nchains, num_samples, target_fn, f_dkdevine, sigma,
        population_sample, times_solve, tspan, f_solve, f_deriv, prior_params, initial_inputs, initial)
    vResults = []
    for i = 1:nchains
         push!(vResults, f_mcmc_nonuniform_growth_factor(num_samples, target_fn, f_dkdevine, sigma,
        population_sample, times_solve, tspan, f_solve, f_deriv, prior_params, initial_inputs, initial))
    end
    return vResults
end

# number of chains (not run in parallel due to RCall)
nchains = 4
# number of MCMC steps (adapting after 100 * length(initial_parametesr))
nsamples = 10000
# MCMC initial (before adaptation) step sizes
sigma = [1.0 * 10^5, 0.05, 0.025, 0.5, 0.0005];
# initial parameters
initial_parameters = [4.0 * 10^5; 0.25; 1.0; 10; 0.01]
dist = MvNormal([2.0 * 10^4, 3.0 * 10^4], [[100000.0 0.0]; [0.0 100000.0]])
vResults = @time f_mcmc_nonuniform_growth_factor_multiple(nchains, nsamples, x -> logpdf(dist, x), dkdevine,
                    sigma, populations_observed, times_observed, tspan,
                    f_solve, deriv_growth_factor,
                    prior_params, initial_parameters, initial_states);

3324.086681 seconds (76.69 M allocations: 5.562 GiB, 0.07% gc time)


Plot target output samples from posterior.

In [12]:
scatter(vResults[1]["outputs"][1000:end, 1], vResults[1]["outputs"][1000:end, 2])